In [1]:
from typing import List, Optional, Any
import torch
import torch.utils.data
import numpy as np
import random

import datetime

import transformers
from transformers import AutoTokenizer, AutoModelForCausalLM, BitsAndBytesConfig

from peft import LoraConfig
from trl import SFTTrainer
import datasets

import json

In [2]:
torch.manual_seed(21)
torch.cuda.manual_seed_all(21)
np.random.seed(21)
random.seed(21)
#torch.backends.cudnn.deterministic = True
#torch.backends.cudnn.benchmark = False

In [3]:
device = torch.device("cuda")

In [4]:
class DatasetNatural2CQL(torch.utils.data.Dataset):
    def __init__(self, path: Optional[str] = None) -> None:
        self.sentence_freq = []
        self.cql2nl = []
        self.nl2cql = []
        self.natural_language_rulebased = []
        self.cql = []
        self.natural_language = []
        self.enabled_natural_language = []

        if path is not None:
            self.load_tsv(path)

    def enable_cql(self, cqls):
        self.enabled_natural_language = []
        for cql in cqls:
            for p in cql:
                self.enabled_natural_language.append(p)

    def dump_json(self, filepath: str) -> None:
        with open(filepath, "w") as file:
            for i in range(len(self)):
                data = json.dumps(self[i])
                file.write(data)
                file.write("\n")

    def add_translation(self, freq: int, cql: str, natural_language_rulebased: str, natural_language: List[str]) -> None:
        cql_index = len(self.sentence_freq)
        self.sentence_freq.append(freq)
        self.cql.append(cql)
        self.natural_language_rulebased.append(natural_language_rulebased)
        self.cql2nl.append([])

        for sentence in natural_language:
            self.nl2cql.append(cql_index)
            self.cql2nl[-1].append(len(self.natural_language))
            self.natural_language.append(sentence)

    def load_tsv(self, path: str) -> None:
        with open(path, "r") as file_data:
            for line in file_data:
                line = line.strip()
                line = line.split("\t")
                texts_json = json.loads(line[4])
                texts_extracted = texts_json["data"][0]["content"][0]["text"]["value"].split("\n")
                self.add_translation(int(line[0]), line[2], line[3], texts_extracted)

    def __len__(self):
        return len(self.enabled_natural_language)

    def __getitem__(self, idx):
        if idx < len(self.nl2cql):
            return {"text": self.natural_language[self.enabled_natural_language[idx]], "cql": self.cql[self.nl2cql[self.enabled_natural_language[idx]]]}
        return None
        

In [5]:
model_name = "meta-llama/Llama-3.2-1B"

bnb_config = BitsAndBytesConfig(
    load_in_4bit=True,
    bnb_4bit_quant_type="nf4",
    bnb_4bit_compute_dtype=torch.bfloat16
)

tokenizer = AutoTokenizer.from_pretrained(model_name)
model = AutoModelForCausalLM.from_pretrained(model_name, quantization_config=bnb_config, device_map={"":0})

In [6]:
dataset = DatasetNatural2CQL("expand_natural_texts_0004.res.tsv")

In [7]:
train_cqls = []
with open("train_ids.json", "r") as file:
    train_cqls = json.load(file)

In [8]:
dataset.enable_cql(train_cqls)

In [9]:
print(len(dataset))
dataset[len(dataset)-1]

84984


{'text': "'ain't', 'no', or 'not' followed by one or two unspecified tokens and resulting in 'nothing', 'nowhere', or 'nobody'.",
 'cql': '[word="ain\'t|no|not"][]{1,2}[word="nothing|nowhere|nobody"]'}

In [10]:
dataset.dump_json("_tmp.json")

In [11]:
lora_config = LoraConfig(
    r=1,
    lora_alpha=2,
    target_modules=["q_proj", "o_proj", "k_proj", "v_proj", "gate_proj", "up_proj", "down_proj"],
    lora_dropout=0.05,
    task_type="CAUSAL_LM",
)

In [12]:
dataset_fancy = datasets.load_dataset("json", data_files="_tmp.json")

Generating train split: 0 examples [00:00, ? examples/s]

In [13]:
def f_in(data):
    full_input = """Translate Natural Language into CQL Queries like:

Word dog followed by lemma run, and then followed by a noun. CQL:
```
[word="dog"][lemma="run"][pos="NN"]
```

Lemma "be" optionally followed by the word "not". CQL:
```
[lemma="be"][word="not"]? 
```

""" + data["text"] + " CQL:\n```\n" + data["cql"] + "```<eos>"
    return tokenizer(full_input, truncation=True, max_length=1024)

In [14]:
dataset_fancy_tokenized = dataset_fancy.map(f_in)

Map:   0%|          | 0/84984 [00:00<?, ? examples/s]

In [15]:
trainer = SFTTrainer(
    model=model,
    train_dataset=dataset_fancy_tokenized["train"],
    args=transformers.TrainingArguments(
        per_device_train_batch_size=4,
        gradient_accumulation_steps=2,
        warmup_steps=100,
        num_train_epochs=10,
        learning_rate=2e-4,
        fp16=True,
        logging_steps=500,
        save_steps=500,
        output_dir="outputs",
        optim="paged_adamw_8bit",
        logging_dir='./logs',
    ),
    peft_config=lora_config,
)

Truncating train dataset:   0%|          | 0/84984 [00:00<?, ? examples/s]

No label_names provided for model class `PeftModelForCausalLM`. Since `PeftModel` hides base models input arguments, if label_names is not given, label_names can't be set automatically within `Trainer`. Note that empty label_names list will be used instead.


In [ ]:
trainer.train()

In [29]:
inputs = tokenizer("<eos>", return_tensors="pt").to(device)
inputs

{'input_ids': tensor([[128000,     27,  85499,     29]], device='cuda:0'), 'attention_mask': tensor([[1, 1, 1, 1]], device='cuda:0')}

In [30]:
full_input = """Translate Natural Language into CQL Queries like:

Word dog followed by lemma run, and then followed by a noun. CQL:
```
[word="dog"][lemma="run"][pos="NN"]
```

Lemma "be" optionally followed by the word "not". CQL:
```
[lemma="be"][word="not"]? 
```

""" + "Any word followed by lemma door as tag noun and then starting with word open within sentence." + " CQL:\n```\n"

inputs = tokenizer(full_input, return_tensors="pt").to(device)

outputs = model.generate(**inputs, max_new_tokens=100)
print(tokenizer.decode(outputs[0], skip_special_tokens=True))

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


Translate Natural Language into CQL Queries like:

Word dog followed by lemma run, and then followed by a noun. CQL:
```
[word="dog"][lemma="run"][pos="NN"]
```

Lemma "be" optionally followed by the word "not". CQL:
```
[lemma="be"][word="not"]? 
```

Any word followed by lemma door as tag noun and then starting with word open within sentence. CQL:
```
[][lemma="door"&tag="N.*"][word="open" & tag="RB.?"]within<s/>```<eos>```<eos>```<eos>```<eos>```<eos>```<eos>```</s>```<eos>```<eos>```<eos>``````<eos>``````<eos>``````<eos>``````<eos>``````<eos>``````<eos>``````<eos>``````<


In [22]:
inputs = tokenizer("translate: Any word. ->", return_tensors="pt").to(device)

outputs = model.generate(**inputs, max_new_tokens=500)
print(tokenizer.decode(outputs[0], skip_special_tokens=True))

Setting `pad_token_id` to `eos_token_id`:128001 for open-end generation.


translate: Any word. -> from: Any word. -> to: Any word.
The term "translate" is a word, "the", "word", "into", "the", "understand".
